# Imports and program variables


In [3]:
import numpy as np
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation, Flatten
from keras.layers import Convolution2D, Conv2D, MaxPooling2D, GlobalAveragePooling2D
from keras.optimizers import Adam
from keras.utils import np_utils
from sklearn import metrics
import pandas as pd

from keras.models import Sequential
from keras.layers.recurrent import LSTM
from keras.layers import Dense
from keras.optimizers import Adam
from keras.utils import to_categorical
from keras.models import Sequential
from keras.layers import Dense, Dropout, Flatten, Activation
from keras.layers import Conv2D, MaxPooling2D
from keras.callbacks import ReduceLROnPlateau,ModelCheckpoint

import sys
sys.path.append('../')
from time_series_dataset_loader import TimeSeriesDatasetLoader

from sklearn.model_selection import train_test_split # to split dataset into train and test
from sklearn import preprocessing
from keras.preprocessing.sequence import pad_sequences

In [7]:
DATASET_PATH = '../../datasets/Original/MFCC_10'


## Setting up train and test datasets

In [18]:
dataset_loader = TimeSeriesDatasetLoader(DATASET_PATH)
X, y = dataset_loader.get_dataset()

In [20]:
X = np.asarray(X)
y = np.asarray(y)

In [19]:
X

[array([[ 0.000000e+00,  0.000000e+00, -6.946144e-01, -1.059247e+00,
         -5.817221e+00, -2.488436e+00,  4.027931e+00,  4.891275e+00,
          2.998316e+00, -1.202488e-02, -6.221664e-01,  2.390062e+00,
         -2.007184e+00,  7.550087e-01, -1.018429e-02, -2.094879e-01],
        [ 1.000000e+00,  1.000000e-01, -8.813763e-02,  6.052008e-01,
         -1.169211e+00, -8.527691e-01,  5.276335e+00,  4.917917e-01,
          1.360283e-01,  1.842510e+00, -3.085505e+00,  8.246675e-01,
         -6.894204e+00, -2.016859e-01, -4.928111e+00, -5.831985e-01],
        [ 2.000000e+00,  2.000000e-01,  8.088617e-01,  3.737381e+00,
          2.593136e-02,  1.315610e-01,  6.270128e+00, -9.577522e-01,
          3.387280e+00,  7.857838e-01, -3.687435e+00, -2.510157e+00,
         -7.158956e+00,  1.941918e+00, -2.853777e+00, -6.314011e-01],
        [ 3.000000e+00,  3.000000e-01,  2.217957e+00, -2.880853e+00,
         -3.099021e+00,  1.021426e-01,  8.492230e+00,  4.531919e+00,
         -3.184071e-01, -4.1685

In [22]:
# Completing with zeros
max_len = len(X[0])
for row in X:
        if len(row) > max_len:
            max_len = len(row)

X = pad_sequences(X, dtype=np.float64, maxlen=max_len, padding='post')

In [6]:
# See X and y details
print(X[:2])
print(X.shape)

print(y[:3])
print(y.shape)

[[[ 0  0 -7 ...  0  2 -2]
  [ 1  0 -7 ...  0  5 -1]
  [ 2  0 -7 ...  1  1 -1]
  ...
  [ 0  0  0 ...  0  0  0]
  [ 0  0  0 ...  0  0  0]
  [ 0  0  0 ...  0  0  0]]

 [[ 0  0 11 ...  0  0 -9]
  [ 1  0 13 ... -1  0 -6]
  [ 2  0 11 ... -6  0 -5]
  ...
  [ 0  0  0 ...  0  0  0]
  [ 0  0  0 ...  0  0  0]
  [ 0  0  0 ...  0  0  0]]]
(1066, 543, 16)
[3 0 1]
(1066,)


In [7]:
# Split the dataset in train and test
X_train, X_test, y_train, y_test = train_test_split(X, y,test_size=0.3)

print("\nX_train:\n")
print(X_train[0][0])
print(X_train.shape)

X_train = np.repeat(X_train[..., np.newaxis], 3, -1)
print(X_train.shape)

print("\nX_test:\n")
print(X_test[0][0])
print(X_test.shape)

X_test = np.repeat(X_test[..., np.newaxis], 3, -1)
print(X_test.shape)

print("\ny_train:\n")
print(y_train[:3])
print(y_train.shape)

print("\ny_test:\n")
print(y_test[:3])
print(y_test.shape)


X_train:

[  0   0  -5 -14   2   3  13   6  18  -4   3   8  -7  11  -4   0]
(746, 543, 16)
(746, 543, 16, 3)

X_test:

[  0   0  -4   0   4   9   2   5   2  13   4   9   8  -1   5 -25]
(320, 543, 16)
(320, 543, 16, 3)

y_train:

[2 4 1]
(746,)

y_test:

[1 6 5]
(320,)


In [8]:
# Create categorical matrices
y_train = to_categorical(y_train)
y_test = to_categorical(y_test)

In [10]:
num_rows = int(X[0].shape[0] / 3)
num_columns = X[0].shape[1] * 3
num_channels = X_train.shape[3]

X_train = X_train.reshape(X_train.shape[0], num_rows, num_columns, num_channels)
X_test = X_test.reshape(X_test.shape[0], num_rows, num_columns, num_channels)

print("\nX_train:\n")
print(X_train[0][0])
print(X_train.shape)

print("\nX_test:\n")
print(X_test[0][0])
print(X_test.shape)


X_train:

[[  0   0   0]
 [  0   0   0]
 [ -5  -5  -5]
 [-14 -14 -14]
 [  2   2   2]
 [  3   3   3]
 [ 13  13  13]
 [  6   6   6]
 [ 18  18  18]
 [ -4  -4  -4]
 [  3   3   3]
 [  8   8   8]
 [ -7  -7  -7]
 [ 11  11  11]
 [ -4  -4  -4]
 [  0   0   0]
 [  1   1   1]
 [  0   0   0]
 [ -5  -5  -5]
 [-14 -14 -14]
 [  2   2   2]
 [  4   4   4]
 [ 12  12  12]
 [  4   4   4]
 [ 21  21  21]
 [ -2  -2  -2]
 [  1   1   1]
 [ 10  10  10]
 [ -3  -3  -3]
 [ 16  16  16]
 [ -3  -3  -3]
 [  0   0   0]
 [  2   2   2]
 [  0   0   0]
 [ -4  -4  -4]
 [-12 -12 -12]
 [  1   1   1]
 [  4   4   4]
 [ 13  13  13]
 [  0   0   0]
 [ 19  19  19]
 [  0   0   0]
 [  1   1   1]
 [ 10  10  10]
 [ -1  -1  -1]
 [ 17  17  17]
 [ -2  -2  -2]
 [ -2  -2  -2]]
(746, 181, 48, 3)

X_test:

[[  0   0   0]
 [  0   0   0]
 [ -4  -4  -4]
 [  0   0   0]
 [  4   4   4]
 [  9   9   9]
 [  2   2   2]
 [  5   5   5]
 [  2   2   2]
 [ 13  13  13]
 [  4   4   4]
 [  9   9   9]
 [  8   8   8]
 [ -1  -1  -1]
 [  5   5   5]
 [-25 -25 -25]


## Building and Compiling Model

In [26]:
# example of tending the vgg16 model
from keras.applications.vgg16 import VGG16
from keras.models import Model
from keras.layers import Dense
from keras.layers import Flatten

# load model without classifier layers
model = VGG16(include_top=False, input_shape=(num_rows, num_columns, num_channels))

# set treinable layers
for layer in model.layers:
    layer.trainable = False

model.get_layer('block5_conv3').trainable = True

# add new classifier layers
flat1 = Flatten()(model.outputs)
class1 = Dense(1024, activation='relu')(flat1)
output = Dense(7, activation='softmax')(class1)

# define new model
model = Model(inputs=model.inputs, outputs=output)

# summarize
model.summary()

Model: "model_2"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 181, 48, 3)        0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 181, 48, 64)       1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 181, 48, 64)       36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 90, 24, 64)        0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 90, 24, 128)       73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 90, 24, 128)       147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 45, 12, 128)       0   

In [27]:
# top-k category accuracy
import functools
import keras
top3_acc = functools.partial(keras.metrics.top_k_categorical_accuracy, k=3)
top3_acc.__name__ = 'top3_acc'

# compile the keras model
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy',top3_acc])

In [ ]:
# Define bath and epochs
batch_size = 1
epochs = 500

lr_reduce = ReduceLROnPlateau(monitor='val_loss', factor=0.9, patience=20, min_lr=0.0000001)
mcp_save = ModelCheckpoint('../models/model_checkpoints/super_default.h5', save_best_only=True, monitor='val_loss', mode='min')
cnnhistory=model.fit(X_train, y_train, batch_size = batch_size, epochs = epochs, validation_data=(X_test, y_test), callbacks=[mcp_save, lr_reduce])

Train on 746 samples, validate on 320 samples
Epoch 1/500
746/746 [==============================] - 127s 170ms/step - loss: 3.5414 - accuracy: 0.1501 - top3_acc: 0.4062 - val_loss: 1.9814 - val_accuracy: 0.1469 - val_top3_acc: 0.4406
Epoch 2/500
746/746 [==============================] - 127s 170ms/step - loss: 1.9482 - accuracy: 0.1421 - top3_acc: 0.4263 - val_loss: 1.9491 - val_accuracy: 0.1312 - val_top3_acc: 0.4563
Epoch 3/500
746/746 [==============================] - 126s 169ms/step - loss: 1.9485 - accuracy: 0.1394 - top3_acc: 0.4088 - val_loss: 1.9498 - val_accuracy: 0.1187 - val_top3_acc: 0.3844
Epoch 4/500
746/746 [==============================] - 123s 165ms/step - loss: 1.9452 - accuracy: 0.1434 - top3_acc: 0.4316 - val_loss: 1.9428 - val_accuracy: 0.1281 - val_top3_acc: 0.4344
Epoch 5/500
746/746 [==============================] - 123s 164ms/step - loss: 1.9485 - accuracy: 0.1434 - top3_acc: 0.4142 - val_loss: 1.9444 - val_accuracy: 0.1281 - val_top3_acc: 0.4250
Epoch 6/5

Epoch 44/500
746/746 [==============================] - 122s 164ms/step - loss: 1.9380 - accuracy: 0.1528 - top3_acc: 0.4343 - val_loss: 1.9480 - val_accuracy: 0.1187 - val_top3_acc: 0.3844
Epoch 45/500
746/746 [==============================] - 124s 166ms/step - loss: 1.9377 - accuracy: 0.1568 - top3_acc: 0.4491 - val_loss: 1.9496 - val_accuracy: 0.1187 - val_top3_acc: 0.3844
Epoch 46/500
746/746 [==============================] - 123s 166ms/step - loss: 1.9381 - accuracy: 0.1555 - top3_acc: 0.4504 - val_loss: 1.9490 - val_accuracy: 0.1187 - val_top3_acc: 0.3844
Epoch 47/500
746/746 [==============================] - 122s 164ms/step - loss: 1.9388 - accuracy: 0.1568 - top3_acc: 0.4410 - val_loss: 1.9494 - val_accuracy: 0.1219 - val_top3_acc: 0.3844
Epoch 48/500
746/746 [==============================] - 122s 164ms/step - loss: 1.9387 - accuracy: 0.1461 - top3_acc: 0.4343 - val_loss: 1.9488 - val_accuracy: 0.1187 - val_top3_acc: 0.3844
Epoch 49/500
746/746 [============================

746/746 [==============================] - 122s 163ms/step - loss: 1.9372 - accuracy: 0.1568 - top3_acc: 0.4196 - val_loss: 1.9480 - val_accuracy: 0.1187 - val_top3_acc: 0.3844
Epoch 131/500
746/746 [==============================] - 122s 163ms/step - loss: 1.9372 - accuracy: 0.1568 - top3_acc: 0.4437 - val_loss: 1.9480 - val_accuracy: 0.1187 - val_top3_acc: 0.3844
Epoch 132/500
746/746 [==============================] - 122s 163ms/step - loss: 1.9371 - accuracy: 0.1568 - top3_acc: 0.4424 - val_loss: 1.9481 - val_accuracy: 0.1187 - val_top3_acc: 0.3969
Epoch 133/500
746/746 [==============================] - 122s 164ms/step - loss: 1.9373 - accuracy: 0.1555 - top3_acc: 0.4397 - val_loss: 1.9478 - val_accuracy: 0.1187 - val_top3_acc: 0.3844
Epoch 134/500
746/746 [==============================] - 123s 165ms/step - loss: 1.9371 - accuracy: 0.1568 - top3_acc: 0.4477 - val_loss: 1.9480 - val_accuracy: 0.1187 - val_top3_acc: 0.3969
Epoch 135/500
746/746 [==============================] - 12

Epoch 173/500
746/746 [==============================] - 122s 164ms/step - loss: 1.9370 - accuracy: 0.1568 - top3_acc: 0.4450 - val_loss: 1.9481 - val_accuracy: 0.1187 - val_top3_acc: 0.3969
Epoch 174/500
746/746 [==============================] - 122s 164ms/step - loss: 1.9369 - accuracy: 0.1568 - top3_acc: 0.4276 - val_loss: 1.9483 - val_accuracy: 0.1187 - val_top3_acc: 0.3844
Epoch 175/500
746/746 [==============================] - 122s 164ms/step - loss: 1.9371 - accuracy: 0.1568 - top3_acc: 0.4223 - val_loss: 1.9480 - val_accuracy: 0.1187 - val_top3_acc: 0.3969
Epoch 176/500
746/746 [==============================] - 122s 164ms/step - loss: 1.9370 - accuracy: 0.1568 - top3_acc: 0.4410 - val_loss: 1.9481 - val_accuracy: 0.1187 - val_top3_acc: 0.3844
Epoch 177/500
746/746 [==============================] - 122s 164ms/step - loss: 1.9370 - accuracy: 0.1568 - top3_acc: 0.4410 - val_loss: 1.9481 - val_accuracy: 0.1187 - val_top3_acc: 0.3969
Epoch 178/500
746/746 [======================

In [ ]:
import matplotlib.pyplot as plt

# PLT History info
plt.plot(cnnhistory.history['loss'])
plt.plot(cnnhistory.history['val_loss'])
plt.title('model loss')
plt.ylabel('loss')
plt.xlabel('epoch')
plt.legend(['train', 'test'], loc='upper left')
plt.show()